In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 5GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/halite/kaggle-environments.zip


Neural Network Agent version nn_call.py

In [2]:
from kaggle_environments.envs.halite.helpers import *

import torch

device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

torch.set_default_tensor_type('torch.FloatTensor')


# NN params
in_channels = 10
middle_channels = 32
policy_channels = 5
value_channels = 1
# middle_layer_count = 1
random_seed = None

# training params
lr = 0.0001
betas = (0.9, 0.999)
gamma = 0.99
# eps_clip = 0.2
alpha_value = 0.8
alpha_entropy = 0

# global variables
my_player_id = 0
player_halite = 0
enemy_halite = 0
current_step = 0
terminal_state = False
eliminated = False
episode_tracking = 0

max_episodes = 100
max_timesteps = 400
update_timestep = 30
min_update_steps = 5
save_interval = 10

# diagnostic stuff
save_replay = False
num_replays = 3
print_probs = False
print_loss = False

max_ships = 20
ship_count = 0


# submission stuff
square_probs = False
eval_setting = False


##################################################################################
##################################################################################
##################################################################################
##################################################################################



import numpy as np

import torch
import torch.nn as nn
import torch.nn.functional as F

from torch.distributions import Categorical

import datetime
import random


class InputBlock(nn.Module):
    def __init__(self):
        super(InputBlock, self).__init__()
        self.conv = nn.Conv2d(in_channels = 10, out_channels = 16, kernel_size = 3, stride = 1)
        self.bn = nn.BatchNorm2d(16)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return F.relu(self.bn(self.conv(state)))

class DenseBlock1(nn.Module):
    def __init__(self):
        super(DenseBlock1, self).__init__()
        self.conv = nn.Conv2d(in_channels = 26, out_channels = 16, kernel_size = 3, stride = 1)
        self.bn = nn.BatchNorm2d(16)

    def forward(self, state):

        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return F.relu(self.bn(self.conv(state)))

class DenseBlock2(nn.Module):
    def __init__(self):
        super(DenseBlock2, self).__init__()
        self.conv = nn.Conv2d(in_channels = 42, out_channels = 16, kernel_size = 3, stride = 1)
        self.bn = nn.BatchNorm2d(16)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return F.relu(self.bn(self.conv(state)))

class DenseBlock3(nn.Module):
    def __init__(self):
        super(DenseBlock3, self).__init__()
        self.conv = nn.Conv2d(in_channels = 58, out_channels = 16, kernel_size = 3, stride = 1)
        self.bn = nn.BatchNorm2d(16)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return F.relu(self.bn(self.conv(state)))

class PolicyBlock(nn.Module):
    def __init__(self):
        super(PolicyBlock, self).__init__()
        self.conv = nn.Conv2d(in_channels = 74, out_channels = 5, kernel_size = 3, stride = 1)
        self.logsoftmax = nn.LogSoftmax(dim = 1)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return self.logsoftmax(self.conv(state)).exp()


class ValueBlock(nn.Module):
    def __init__(self):
        super(ValueBlock, self).__init__()
        self.conv = nn.Conv2d(in_channels = 74, out_channels = 1, kernel_size = 3, stride = 1)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        state = F.relu(self.conv(state))
        return state

class ActorCritic(nn.Module):
    def __init__(self):
        super(ActorCritic, self).__init__()

        self.input_conv = InputBlock().to(device)

        self.dense1 = DenseBlock1().to(device)
        self.dense2 = DenseBlock2().to(device)
        self.dense3 = DenseBlock3().to(device)

        self.policy_out = PolicyBlock().to(device)
        self.value_out = ValueBlock().to(device)

    def forward(self):
        raise NotImplementedError

    def get_action_output(self, state):
        temp1 = self.input_conv(state)
        temp1 = torch.cat((state, temp1), dim = 1)

        temp2 = self.dense1(temp1)
        temp2 = torch.cat((temp1, temp2), dim = 1)

        temp3 = self.dense2(temp2)
        temp3 = torch.cat((temp2, temp3), dim = 1)

        temp4 = self.dense3(temp3)
        temp4 = torch.cat((temp3, temp4), dim = 1)

        action_map = self.policy_out(temp4)

        return action_map

    def get_actions(self, state, ship_dict, memory):
        action_map = self.get_action_output(state)
        batch_size = state.size()[0]
        action_dict = {}

        new_ship_locs = state[0][1].detach().clone()
        for ship_id in ship_dict.keys():
            # ship action vector represented by first 6 layers of action output
            ship_loc = ship_dict[ship_id][0]
            ship_loc = (ship_loc // 21, ship_loc % 21)
            if ship_id in memory.states.keys():
                memory.states[ship_id].append(state)
                memory.locations[ship_id].append(ship_loc)
            else:
                memory.states[ship_id] = [state]
                memory.locations[ship_id] = [ship_loc]


            actionprobs = torch.stack((action_map[0][0][ship_loc[0]][ship_loc[1]],
                                       action_map[0][1][ship_loc[0]][ship_loc[1]],
                                       action_map[0][2][ship_loc[0]][ship_loc[1]],
                                       action_map[0][3][ship_loc[0]][ship_loc[1]],
                                       action_map[0][4][ship_loc[0]][ship_loc[1]]))

            if print_probs == True:
                print(actionprobs)
            if square_probs == True:
                actionprobs = torch.mul(actionprobs, actionprobs)

            # action masking
            mask = [1, 1, 1, 1, 1]
            # north
            if new_ship_locs[(ship_loc[0]-1)%21, ship_loc[1]] == 1:
                mask[0] = 0
            # east
            if new_ship_locs[ship_loc[0], (ship_loc[1]+1)%21] == 1:
                mask[1] = 0
            # south
            if new_ship_locs[(ship_loc[0]+1)%21, ship_loc[1]] == 1:
                mask[2] = 0
            # west
            if new_ship_locs[ship_loc[0], (ship_loc[1]-1)%21] == 1:
                mask[3] = 0
            # wait logic
            if mask[0] + mask[1] + mask[2] + mask[3] == 0:
                mask[4] = 1
            elif state[0][3][ship_loc] == 1:
                mask[4] = 0

            actionprobs = torch.mul(actionprobs, torch.tensor(mask).to(device))

            dist = Categorical(actionprobs)
            action = dist.sample()

            action_dict[ship_id] = action
            if ship_id in memory.actions.keys():
                memory.actions[ship_id].append(action)
                memory.logprobs[ship_id].append(dist.log_prob(action))
                memory.conflict_maps[ship_id].append(new_ship_locs.detach().clone())
            else:
                memory.actions[ship_id] = [action]
                memory.logprobs[ship_id] = [dist.log_prob(action)]
                memory.conflict_maps[ship_id] = [new_ship_locs.detach().clone()]

            # update ship loc
            # north
            if action == 0:
                new_ship_locs[(ship_loc[0]-1)%21, ship_loc[1]] = 1
                new_ship_locs[ship_loc[0], ship_loc[1]] = 0
            # east
            elif action == 1:
                new_ship_locs[ship_loc[0], (ship_loc[1]+1)%21] = 1
                new_ship_locs[ship_loc[0], ship_loc[1]] = 0
            # south
            elif action == 2:
                new_ship_locs[(ship_loc[0]+1)%21, ship_loc[1]] = 1
                new_ship_locs[ship_loc[0], ship_loc[1]] = 0
            # west
            elif action == 3:
                new_ship_locs[ship_loc[0], (ship_loc[1]-1)%21] = 1
                new_ship_locs[ship_loc[0], ship_loc[1]] = 0

        return action_dict, new_ship_locs

    def get_logprobs_entropies(self, key, memory):
        # occurs during update, ship_dict should only be a single ship
        logprobs = []
        entropies = []
        for idx in range(len(memory.states[key])):
            state = memory.states[key][idx]
            action_map = self.get_action_output(state)
            ship_loc = memory.locations[key][idx]
            conflict_map = memory.conflict_maps[key][idx]

            actionprobs = torch.stack((action_map[0][0][ship_loc[0]][ship_loc[1]],
                                       action_map[0][1][ship_loc[0]][ship_loc[1]],
                                       action_map[0][2][ship_loc[0]][ship_loc[1]],
                                       action_map[0][3][ship_loc[0]][ship_loc[1]],
                                       action_map[0][4][ship_loc[0]][ship_loc[1]]))

            # action masking
            mask = [1, 1, 1, 1, 1]
            # north
            if conflict_map[(ship_loc[0]-1)%21, ship_loc[1]] == 1:
                mask[0] = 0
            # east
            if conflict_map[ship_loc[0], (ship_loc[1]+1)%21] == 1:
                mask[1] = 0
            # south
            if conflict_map[(ship_loc[0]+1)%21, ship_loc[1]] == 1:
                mask[2] = 0
            # west
            if conflict_map[ship_loc[0], (ship_loc[1]-1)%21] == 1:
                mask[3] = 0
            # wait logic
            if mask[0] + mask[1] + mask[2] + mask[3] == 0:
                mask[4] = 1
            elif state[0][3][ship_loc] == 1:
                mask[4] = 0

            actionprobs = torch.mul(actionprobs, torch.tensor(mask).to(device))

            dist = Categorical(actionprobs)

            logprobs.append(dist.log_prob(memory.actions[key][idx]))
            entropies.append(dist.entropy())


        logprobs = torch.stack(logprobs).to(device)
        entropies = torch.stack(entropies).to(device)

        return logprobs, entropies

    def get_value_map(self, state):
        temp1 = self.input_conv(state)
        temp1 = torch.cat((state, temp1), dim = 1)

        temp2 = self.dense1(temp1)
        temp2 = torch.cat((temp1, temp2), dim = 1)

        temp3 = self.dense2(temp2)
        temp3 = torch.cat((temp2, temp3), dim = 1)

        temp4 = self.dense3(temp3)
        temp4 = torch.cat((temp3, temp4), dim = 1)

        value_map = self.value_out(temp4)

        return value_map[0][0]



##################################################################################
##################################################################################
##################################################################################
##################################################################################



import torch

import datetime

def process_state(state):
    current_player = state.player

    halite_plane = np.reshape(np.array(state.halite), (21, 21))

    ally_ship_plane = np.zeros([441])
    ally_cargo_plane = np.zeros([441])
    ally_yard_plane = np.zeros([441])
    enemy_ship_plane = np.zeros([441])
    enemy_cargo_plane = np.zeros([441])
    enemy_yard_plane = np.zeros([441])
    empty_plane = np.full([441], 1)

    for player_id in range(len(state.players)):
        if player_id == current_player:
            # state.observation.players[player_id][2] is the dictionary of ships with key being ship ID
            # and value being [location, cargo amount]
            for ship in state.players[player_id][2].keys():
                ally_ship_plane[state.players[player_id][2][ship][0]] = 1
                ally_cargo_plane[state.players[player_id][2][ship][0]] = state.players[player_id][2][ship][1]
                empty_plane[state.players[player_id][2][ship][0]] = 0
            for yard in state.players[player_id][1].keys():
                ally_yard_plane[state.players[player_id][1][yard]] = 1
                empty_plane[state.players[player_id][1][yard]] = 0
        else:
            for ship in state.players[player_id][2].keys():
                enemy_ship_plane[state.players[player_id][2][ship][0]] = 1
                enemy_cargo_plane[state.players[player_id][2][ship][0]] = state.players[player_id][2][ship][1]
                empty_plane[state.players[player_id][2][ship][0]] = 0
            for yard in state.players[player_id][1].keys():
                enemy_yard_plane[state.players[player_id][1][yard]] = 1
                empty_plane[state.players[player_id][1][yard]] = 0

    ally_ship_plane = np.reshape(ally_ship_plane, (21, 21))
    ally_cargo_plane = np.reshape(ally_cargo_plane, (21, 21))
    ally_yard_plane = np.reshape(ally_yard_plane, (21, 21))
    enemy_ship_plane = np.reshape(enemy_ship_plane, (21, 21))
    enemy_cargo_plane = np.reshape(enemy_cargo_plane, (21, 21))
    enemy_yard_plane = np.reshape(enemy_yard_plane, (21, 21))
    empty_plane = np.reshape(empty_plane, (21, 21))


    halite_plane = np.divide(halite_plane, 500)
    ally_cargo_plane = np.divide(ally_cargo_plane, 500)
    enemy_cargo_plane = np.divide(enemy_cargo_plane, 500)

    player_halite_plane = np.full([441], player_halite)
    player_halite_plane = np.reshape(player_halite_plane, (21, 21))
    player_halite_plane = np.divide(player_halite_plane, 500)

    timestep_plane = np.full([441], current_step)
    timestep_plane = np.reshape(timestep_plane, (21, 21))
    timestep_plane = np.divide(timestep_plane, 400)

    output = np.stack((halite_plane, ally_ship_plane, ally_cargo_plane, ally_yard_plane,
                     enemy_ship_plane, enemy_cargo_plane, enemy_yard_plane, empty_plane,
                     player_halite_plane, timestep_plane))

    return torch.unsqueeze(torch.tensor(output).float().to(device), 0)




##################################################################################
##################################################################################
##################################################################################
##################################################################################

import base64

model_string = b'...'


decoded_model = base64.b64decode(model_string)


##################################################################################
##################################################################################
##################################################################################
##################################################################################


import numpy as np

import torch
import torch.nn as nn
from io import BytesIO


class Memory:
    def __init__(self):
        self.actions = {}
        self.locations = {}
        self.next_locations = {}
        self.logprobs = {}
        self.rewards = {}
        self.states = {}
        self.next_states = {}
        self.conflict_maps = {}

    def clear(self):
        self.actions = {}
        self.locations = {}
        self.next_locations = {}
        self.logprobs = {}
        self.rewards = {}
        self.states = {}
        self.next_states = {}
        self.conflict_maps = {}

class PPO:
    def __init__(self):
        # hyperparams defined in config.py
        self.lr = lr
        self.betas = betas
        self.gamma = gamma


        self.policy = ActorCritic()
        if eval_setting == True:
            self.policy.eval()
        self.policy.float()
        self.policy.to(device)

        self.policy.load_state_dict(torch.load(BytesIO(decoded_model)))

        self.optimizer = torch.optim.Adam(self.policy.parameters(), lr = self.lr, betas = self.betas)





##################################################################################
##################################################################################
##################################################################################
##################################################################################





import torch
import torch.nn as nn

import numpy as np

from kaggle_environments import make






ppo = PPO()
memory = Memory()

def NN_call(obs, config, ship_dict):
	state = obs
	if isinstance(state, list):
		state = state[0]

	my_player_id = state.player

	submit_dict = {}

	ship_action_translate = {0: 'NORTH', 1: 'EAST', 2: 'SOUTH', 3: 'WEST', 4: 'WAIT'}

	player_halite = state.players[my_player_id][0]

	state_grid = process_state(state)

	action_dict, new_ship_locs = ppo.policy.get_actions(state_grid, ship_dict, memory)


	for key in ship_dict.keys():
        	if action_dict[key].item() != 4:
        		submit_dict[key] = ship_action_translate[action_dict[key].item()]


	memory.clear()

	return submit_dict


Hard coded agent

In [3]:
%%writefile submission.py

from kaggle_environments.envs.halite.helpers import *
import numpy as np # linear algebra
import random

class Agent(object):
    
    def __init__(self,obs,config): 
        self.obs = obs
        self.config = config
        self.size=config.size
        self.board=Board(obs,config)
        self.me=self.board.current_player
        self.enemy_ships=[ship for ship in self.board.ships.values() if ship not in self.me.ships]
        self.enemy_shipyards = [shipyard for shipyard in self.board.shipyards.values() if shipyard not in self.me.shipyards]
        self.cost = 500

        #retreat
        self.enemyRetreatRadius=2
        
        #earlyLateGame
        self.earlyGameTurn = 10
        
        #shipyardDefense
        self.defenderRadius = 4
        
        #mining
        self.minHaliteToDeposit = 500
        self.collectRadiusToScan = 3
        self.minHaliteToMine = 100
        
        #spawn
        self.minHaliteToSpawn = 1050
        self.maxShips = 25
        self.maxRoundToSpawn = 270
        
        #attackShip
        self.enemyCollisionRadius = 2
        
        #attackShipyard
        self.enemyShipyardCollisionRadius = 4
        self.maxCargoToAllowDestroyingShipyard = 100
        


    # Directions a ship can move
    directions = [ShipAction.NORTH, ShipAction.EAST, ShipAction.SOUTH, ShipAction.WEST]
    
    # Will keep track of whether a ship is collecting halite or carrying cargo to a shipyard
    # Dict[ShipId,str]
    ship_states = {}
    
    # Will kepp track of shipyard defenders 
    # Dict[ShipyardId,ShipId]
    shipyard_defenders = {}
    
    """
    takes vector with coordinates in [-size,-size], and do arithmetic modulo size on [-size/2,size/2].
       Parameters:
        x : int in range [-size,size], x coordinate of a point on the grid
        y : int in range [-size,size], y coordinate of a point on the grid
       Returns:
        Tuple, (x,y) with coordinates in range [-size/2,size/2]
    """
    def vectorMod(self,x,y):
        halfsize=np.floor(self.size/2)
        x=((x+halfsize) %self.size )-halfsize
        y=((y+halfsize) %self.size )-halfsize
        return (x,y)            
    
    
    """
    Returns Tuple
    """
    def getDirToTuple(self,fromPos, toPos):
        if fromPos == toPos:
            return None #return None if positions are the same
        a= toPos[0]-fromPos[0]
        b= toPos[1]-fromPos[1]
        c=self.vectorMod(a,b)  
        retX = ShipAction.EAST
        retY = ShipAction.NORTH
        if c[0]<0: retX = ShipAction.WEST
        if c[1]<0: retY = ShipAction.SOUTH
        if c[0]==0: return None, retY #same axis
        if c[1]==0: return retX, None #same axis
        return retX, retY
    
    """
    Takes two positions and return a direction to move from first to second point, taking into account map wrapping.
    If the position are the same it returns None.
    Also checks to see if the direction to move to contains any ships or shipyards and priorotizes the empty cell path.
       Parameters:
        fromPos : Point, (x,y) in range [0,size]
        toPos : Point, (x,y) in range [0,size]
       Returns:
        ShipAction, direction from fromPos to toPos, chosen based on if one direction leads to empty cell
    """
    def getDirTo(self,fromPos, toPos):      
        direction = self.getDirToTuple(fromPos, toPos)
        if direction == None:
            return None
        if direction[0]== None:
            return direction[1]
        if direction[1]==None:
            return direction[0]
        retX=direction[0]
        retY=direction[1]
        #Getting here means there are two directions to consider
        retXCell=self.board[fromPos.translate(retX.to_point(),self.size)] #Cell to which ship will get to if goes in retX dir
        retYCell=self.board[fromPos.translate(retY.to_point(),self.size)] #Cell to which ship will get to if goes in retY dir
        retXBool=retXCell.ship!=None or retXCell.shipyard!=None #True iff retXCell has ship or shipyard in it
        retYBool=retYCell.ship!=None or retYCell.shipyard!=None #True iff retYCell has ship or shipyard in it
        if (retXBool and retYBool) or (not retXBool and not retYBool) :
            if random.randint(0, 1)==0: return retX  
            else: return retY
        else: 
            if retXBool:
                return retY
            else:
                return retX

    """
    Same as getDirTo but priorotizes based on higher halite between the directions.
       Parameters:
        fromPos : Point, (x,y) in range [0,size]
        toPos : Point, (x,y) in range [0,size]
       Returns:
        ShipAction, direction from fromPos to toPos, chosen based on higher halite in the cell direction
    """
    def getDirTo_halite(self,fromPos, toPos):
        if fromPos == toPos:
            return None #return None if positions are the same
        a= toPos[0]-fromPos[0]
        b= toPos[1]-fromPos[1]
        c=self.vectorMod(a,b)    
        retX = ShipAction.EAST
        retY = ShipAction.NORTH
        if c[0]<0: retX = ShipAction.WEST
        if c[1]<0: retY = ShipAction.SOUTH
        if c[0]==0: return retY #same axis
        if c[1]==0: return retX #same axis
        #Getting here means there are two directions to consider
        retXCell=self.board[fromPos.translate(retX.to_point(),self.size)] #Cell to which ship will get to if goes in retX dir
        retYCell=self.board[fromPos.translate(retY.to_point(),self.size)] #Cell to which ship will get to if goes in retY dir
        if retXCell.halite>retYCell.halite:
            return retX
        else: return retY
            

    """
    takes two positions and return the distance between them, taking into account map wrapping
       Parameters:
        fromPos : Point, (x,y) in range [0,size]
        toPos :  (x,y) in range [0,size]
       Returns:
        an integer in range [0,size]
    """
    def distFromTo(self,fromPos,toPos):
        a= toPos[0]-fromPos[0]
        b= toPos[1]-fromPos[1]
        c=self.vectorMod(a,b)
        return abs(c[0])+abs(c[1])

    """
    Returns a cell containing the maximum halite in a 2*radius+1 box around ship
       Parameters:
        ship : ShipId
        radius : int in range [0,size]
       Returns:
        Cell, a cell on the board
    """
    def maxHalitePos(self,ship,radius):
        x = ship.cell.position.x
        y = ship.cell.position.y
        cells = [self.board[ship.position.translate((a,b),self.size)] for a in range(x-radius,x+radius+1) for b in range(y-radius,y+radius+1)]
        cellhalite=[c.halite for c in cells]
        maxcell=cells[np.argmax(cellhalite)]
        return maxcell
    #for applications, perhaps more efficient to have collector one collect maxhalite, collector two second most maxhalite, etc


    """
    Takes a list of objects(ships or shipyards) and returns it sorted by their distance to a specified position
    (lower index means less distance). Returns None if there list is empty or position is None
       Parameters:
        L : list of objects (ships or shipyards)
        pos : position on board.
       Returns:s
        List[object], sorted list of ships or shipyards
    """
    def sortByDistFromPos(self,L,pos):
        if len(L)==0:
            return None
        return sorted(L,key=lambda x: self.distFromTo(x.position,pos))
 
    """
    Returns the opposite direction to a direction
       Parameters:
        direction: ShipAction
       Returns:
        ShipAction
    """
    def oppositeDir(self,direction):
        if direction:
            return self.directions[(self.directions.index(direction)+2)%4]

    """
    Finds enemy one rank away from you in terms of halite (prioritizing higher rank)
       Parameters:
        player: PlayerId, typically me
       Returns:
        PlayerId, an enemy player
    """
    def closestEnemyHalite(self,player): 
        players_halite = {p : p.halite for p in self.board.opponents}
        if len(players_halite)==1:
            return player
        if len(players_halite)==0:
            return None
        players_halite = sorted(players_halite.items(), key=lambda x: x[1], reverse=True)
        player_index = players_halite.index((player,player.halite))
        if player_index==0:
            return players_halite[1][0]
        else:
            return players_halite[player_index-1][0]

    """
    Finds all ships with low halite for one player
       Parameters:
        shipss: list of ShipId
       Returns:
        list of ShipId
    """
#     def shipsslowhalite(self,shipss,lowhalitecounter):
#         return [s for s in shipss if s.halite<lowhalitecounter]

    """
    Finds ship with lowest halite not in shipsslowhalite(), or highest halite in shipsslowhalite() if former list is empty
       Parameters:
        play: PlayerId, typically me
       Returns:
        ShipId
    """
#     def shipsslowesthalite(self,play):
#         if play.ships==[]:
#             return None
#         if len(play.ships)>0:
#             abovelowhaliteships=[s for s in play.ships if s not in shipsslowhalite(self,play.ships,lowhalitecounter)]
#             if abovelowhaliteships==[]:
#                 shipcan=shipsslowhalite(play.ships)[0]
#                 for ss in shipcan:
#                     if ss.halite>shipcan.halite:
#                         ss=shipcan
#                 return shipcan
#             if len(abovelowhaliteships)>0:
#                 shipcan=abovelowhaliteships[0]
#                 for s in abovelowhaliteships:
#                     if s.halite<shipcan.halite:
#                         s=shipcan
#                 return shipcan
    
    """
    Finds closest enemy shipyard of player considered in closestEnemyHalite() relative to shipsslowhalite()
       Parameters:
        shipss: list of ShipId
       Returns:
        Tuple (ene,my)
            ene: ShipyardId, an enemy shipyard
            my: ShipId, a ship that is among shipsslowhalite()
    """
#     def closestenemyShipyardrelship(shipss):
#         if shipss==None:
#             return None
#         ene1=opponentHalite(me)
#         if ene1==None:
#             return None
#         if len(ene1.shipyards)==0:
#             return None
#         ene=ene1.shipyards[0]
#         if shipsslowhalite(shipss)==[]:
#             return None
#         my=shipsslowhalite(shipss)[0]
#         for x in opponentHalite(me).shipyards:
#             for y in shipsslowhalite(shipss):
#                 if distFromTo(ene.position,my.position) > distFromTo(x.position,y.position):
#                     ene=x
#                     my=y
#         tup=(ene,my)
#         return tup
    

    
#     def shouldShipyardSpawn(shipyard):
#         spawnCostMultiplier = 3
#         stepInterval = 10
#         shipsPerShipyard = 4
#         maxRoundToSpawn = 300
#         if me.halite>spawnCostMultiplier*config.spawnCost and board.step%stepInterval == 0 and len(me.ships)<shipsPerShipyard*len(me.shipyards) and board.step<maxRoundToSpawn:
#             return True
#         return False
    
    


    #Action Functions
    # functions here should input List[Ship] and output a Dict[ShipId,str]
    
    # returns a tuple of (Dict[ShipId,str],Dict[ShipyardId,str])
    def earlyLateGame(self,ships,shipyards,turn):
        if len(ships)==0 and len(shipyards)==0:
            return None 
        retShips={ship.id:'NOACTION' for ship in ships}
        retShipyards={shipyard.id: 'NOACTION' for shipyard in shipyards}
        
        #early game
        if self.board.step>=1 and self.board.step<=turn:
            retShipyards[shipyards[0].id] = ShipyardAction.SPAWN
              
        #late game
        if self.board.step==398:
            for ship in ships:
                if ship.halite>self.cost:
                    retShips[ship.id] = ShipAction.CONVERT
        
        return retShips, retShipyards
    
    """
    Determines if a ship should be converted to a shipyard based on distances between shipyards and halite collected
       Parameters:
        ship: ShipId, an ally ship
       Returns:
        Boolean, either True or False
    """
#     def shouldShipConvert(ship):
#         if len(me.shipyards) == 0:
#             return False10
#         shipyardMinDist = 7
#         maxShipyards = 3
#         convertCostMultiplier = 5
#         if distFromTo(ship.position,closestAllyShipyard(ship).position)>shipyardMinDist and (ship.halite+me.halite)>convertCostMultiplier*config.convertCost and len(me.shipyards)<maxShipyards:
#             return True
#         return False
    
    def convert(self,play,ships):
        if len(ships)==0:
            return None 
        ret={ship.id:'NOACTION' for ship in ships}
        # If there are no shipyards, convert first ship into shipyard.
        if len(play.shipyards) == 0:
            ret[ships[0].id] = ShipAction.CONVERT
        return ret
    
    """
    
    """    
    def spawn(self,play,shipyards,minHaliteToSpawn,maxShips,maxRoundToSpawn):
        if len(shipyards)==0:
            return None
        ret={shipyard.id: 'NOACTION' for shipyard in shipyards}
        # If there are no ships, use first shipyard to spawn a ship.
        if len(play.ships) == 0 and play.halite>=self.cost:
            ret[shipyards[0].id] = ShipyardAction.SPAWN
                        
        for shipyard in shipyards:       
                if play.halite>minHaliteToSpawn and len(play.ships)<maxShips and self.board.step<maxRoundToSpawn:
                    ret[shipyard.id] = ShipyardAction.SPAWN
        
        return ret
    
        """
    If halite at current location of ship running low, move to a square nearby containing the most halite
       Parameters:
        ship: ShipId, an ally ship
       Returns:
        ShipAction
    """
    def collect(self,ship,collectRadiusToScan,minHaliteToMine):
        if ship.cell.halite < minHaliteToMine:
            C = self.maxHalitePos(ship,collectRadiusToScan)
            direction = self.getDirTo(ship.position, C.position)
            if random.randint(0, 8)==0: #randomize move with certain percentage
                direction = self.directions[random.randint(0,3)]
            return direction
        return None
        
      
    """
    Returns best direction for ship to deposit cargo, chosen randomly if more than 1 exists
       Parameters:
        ship: ShipId, an ally ship
       Returns:
        ShipAction
    """
    def deposit(self,play,ship):
        # Move towards shipyard to deposit cargo
        closestAllyShipyard=self.sortByDistFromPos(play.shipyards,ship.position)
        if closestAllyShipyard==None:
            return None
        closestAllyShipyard=closestAllyShipyard[0]
        return self.getDirTo(ship.position,closestAllyShipyard.position)
        
    def mining(self,play,ships,minHaliteToDeposit,collectRadiusToScan,minHaliteToMine):
        if len(ships)==0:
            return None 
        ret={ship.id:'NOACTION' for ship in ships}
        for ship in ships:
            if ship.halite <= minHaliteToDeposit: # If cargo is too low, collect halite
                ret[ship.id] = self.collect(ship,collectRadiusToScan,minHaliteToMine)
            else: # If cargo gets very big, deposit halite
                ret[ship.id] = self.deposit(play,ship)
        return ret
        
    
    def attackShip(self,ships,enemyCollisionRadius):
        if len(ships)==0:
            return None 
        ret={ship.id:'NOACTION' for ship in ships}
        
        """ according to doc we should comment this"""
        if len(self.enemy_ships)>0 and None not in self.enemy_ships:
            #if self.board.step<=20:
             #   print(self.enemy_ships)
            for ship in ships: 
                closestEnemy = self.sortByDistFromPos(self.enemy_ships,ship.position)
                if closestEnemy != None:
                    closestEnemy = self.sortByDistFromPos(self.enemy_ships,ship.position)[0]
                    if self.distFromTo(ship.position,closestEnemy.position)<=enemyCollisionRadius: #if enemy is close            
                        if ship.halite < closestEnemy.halite: #you are going to win the duel
                            ret[ship.id]=self.getDirTo(ship.position,closestEnemy.position)
        """" to here """
        
        return ret
    
    #Returns Dict[ShipId,List[ShipAction]] of restricted actions. Note that this actually returns the directions that 
    #you want to avoid.
    def retreat(self,ships,enemyRetreatRadius):
        if len(ships)==0:
            return None 
        ret={ship.id:[] for ship in ships}
        for ship in ships: 
            closestEnemy = self.sortByDistFromPos(self.enemy_ships,ship.position)
            if closestEnemy != None:
                closestEnemy = self.sortByDistFromPos(self.enemy_ships,ship.position)[0]
                if self.distFromTo(ship.position,closestEnemy.position)<=enemyRetreatRadius: #if enemy is close            
                    if ship.halite >= closestEnemy.halite: #you are going to lose the duel
                        direction = self.getDirToTuple(ship.position,closestEnemy.position)
                        if direction[0]==None: #ships are on the same axis
                            ret[ship.id].append(direction[1])
                        if direction[1]==None: #ships are on the same axis
                            ret[ship.id].append(direction[0])
                        else: 
                            ret[ship.id].extend(direction)         
        return ret
    
    def attackShipyard(self,ships,enemyShipyardCollisionRadius,maxCargoToAllowDestroyingShipyard):
        if len(ships)==0:
            return None 
        ret={ship.id:'NOACTION' for ship in ships}
        for ship in ships:
            enemyShipyard = self.sortByDistFromPos(self.enemy_shipyards,ship.position)
            if enemyShipyard != None:
                enemyShipyard = enemyShipyard[0]
                if self.distFromTo(ship.position,enemyShipyard.position)<=enemyShipyardCollisionRadius and ship.halite < maxCargoToAllowDestroyingShipyard:
                    ret[ship.id] = self.getDirTo(ship.position,enemyShipyard.position)
        return ret

    
    """
    Designates a ship as the shipyard defender and stays on the shipyard if enemy ship is <=2 dist away
    otherwise it stays 1 distance away from the shipyard to allow for deposit/spawn. 
        Parameters:
         ships: List[Ship], list of all allied ships
         shipyard: Shipyard, shipyard to be protected
         radius: int, the radius around shipyard to scan for ships to move away from
        Returns:
         Dict[str,str], key=ShipId, val=action
         or None if shipyard is None or ships is empty
         
         Remarks: what happens if the same ship is the defender of two different shipyards or len(ships)==1?
         another possible problem, when defender waits dist 1 from shipyard it might collect halite and lose fight
         option to consider: make defender move to shipyard everytime its distance 1.
    """
    def shipyardDefense(self,play,ships,radius): #fix to not have shipyard here.
        if len(ships)==0:
            return None 
        ret={ship.id:'NOACTION' for ship in ships}
        if len(play.shipyards)==0:
            self.shipyard_defenders.clear()
            return ret
        shipyard=play.shipyards[0] #in order to fix for all shipyards need to loop and make sure no same defenders
        #designate defender
        defender=None
        find=True
        if shipyard.id in self.shipyard_defenders.keys():
            if self.shipyard_defenders[shipyard.id] in self.board.ships:  
                defender = self.board.ships[self.shipyard_defenders[shipyard.id]]
            if defender!=None: 
                find=False
            else: #defender ship died last turn
                self.shipyard_defenders.pop(shipyard.id)
        if find:
            defender = self.sortByDistFromPos(ships,shipyard.position)[0]
            self.shipyard_defenders[shipyard.id] = defender.id
                   
        distance=self.distFromTo(defender.position,shipyard.position)
        #if defender distance from shipyard is not 1, send it to shipyard.
        if distance > 1:
            ret[defender.id]=self.getDirTo(defender.position,shipyard.position)
            return ret
        closestEnemyShip=self.sortByDistFromPos(self.enemy_ships,shipyard.position)
        if closestEnemyShip:
            closestEnemyShip=self.sortByDistFromPos(self.enemy_ships,shipyard.position)[0] #closeset enemy ship to shipyard
        else: #there are no enemy ships
            ret[defender.id]=None
            return ret
        #defender is on shipyard
        if distance==0:
            if self.distFromTo(closestEnemyShip.position,shipyard.position) <=2:
                ret[defender.id]=None
                return ret
            else: #Move to direction which is least congested with ships
                L=self.sortByDistFromPos(self.board.ships.values(),shipyard.position)
                LRadius=[ship for ship in L if self.distFromTo(ship.position,shipyard.position)<=radius]
                LRadiusPos=[(ship.position-shipyard.position) for ship in LRadius]
                LRadiusDir=[self.vectorMod(pos[0],pos[1]) for pos in LRadiusPos]
                LNorth=[v for v in LRadiusDir if v[1]>0]
                LSouth=[v for v in LRadiusDir if v[1]<0]
                LEast=[v for v in LRadiusDir if v[0]>0]
                LWest=[v for v in LRadiusDir if v[0]<0]
                Congested = {0:len(LNorth),1:len(LEast),2:len(LSouth),3:len(LWest)}
                ret[defender.id]=self.directions[(sorted(Congested.items(), key=lambda x: x[1])[0][0])]
                return ret
        else: #distance==1, defender is neighbour to shipyard
            #if enemy ships is close, defender has halite or a coin toss is heads then return to shipyard
            if self.distFromTo(closestEnemyShip.position,shipyard.position) <=2 or defender.halite>0 or random.randint(0, 1)==0: 
                ret[defender.id]=self.getDirTo(defender.position,shipyard.position)
                return ret
            else:
                ret[defender.id]=None
                return ret 
    
    
    
    
    
    
    
    
    
    
    
    
    
    
    """
    Gives plausible actions of a ship sorted by priority, and if action coincides with retreat make it 'NOACTION'
       Parameters:
        play: PlayerId
       Returns:
        Tuple of dictionary with
            Key: ShipId and ShipyardId
            Values: list of ShipyardActions or ShipActions
    """
    def ActionPriorityList(self,play):
        lis=[]
        lisy=[]
        afs=[ShipAction.NORTH, ShipAction.EAST, ShipAction.SOUTH, ShipAction.WEST, None]
        actions=[self.earlyLateGame(play.ships,play.shipyards,self.earlyGameTurn)[0],'NOACTION',self.shipyardDefense(play,play.ships,self.defenderRadius),self.convert(play,play.ships),self.attackShip(play.ships,self.enemyCollisionRadius), 
           self.attackShipyard(play.ships,self.enemyShipyardCollisionRadius,self.maxCargoToAllowDestroyingShipyard),self.mining(play,play.ships,self.minHaliteToDeposit,self.collectRadiusToScan,self.minHaliteToMine)]
        for ship in play.ships:        
            #7 items in l
            l=[action[ship.id] for action in actions if action!='NOACTION']
            others=[]
            for a in afs:
                if a not in l:
                    others.append(a)
            random.shuffle(others) #randomly shuffles the other actions; by adding this, SelfCollision() will not output a list of actions where nothing moves
            l.extend(others)
            for n,action in enumerate(l):
                if action in self.retreat(play.ships,self.enemyRetreatRadius)[ship.id]: #deletes actions that will make enemy collide with you
                    l[n]='NOACTION'
            lis.append(l)
        sy_actions=[self.earlyLateGame(play.ships,play.shipyards,self.earlyGameTurn)[1],self.spawn(play,play.shipyards,self.minHaliteToSpawn,self.maxShips,self.maxRoundToSpawn),
               'NOACTION','NOACTION','NOACTION','NOACTION','NOACTION']
        for shipyard in play.shipyards:
#             l=[self.earlyLateGame(play.ships,play.shipyards,self.earlyGameTurn)[1][shipyard.id],self.spawn(play,play.shipyards,self.minHaliteToSpawn,self.maxShips,self.maxRoundToSpawn)[shipyard.id],'NOACTION','NOACTION','NOACTION','NOACTION','NOACTION']
            l=[action[shipyard.id] for action in sy_actions if action!='NOACTION']
            if l[0]!=None or l[1]!=None:
                l.append(None)
            lisy.append(l)
        names = play.ship_ids
        namesy = play.shipyard_ids
        return dict(zip(names,lis)), dict(zip(namesy,lisy))
    
    """
    Return non-'NOACTION' actions in ActionPriorityList()
       Parameters:
        play: PlayerId
       Returns:
        Tuple of dictionary with
            Key: ShipId and ShipyardId
            Values: list of ShipyardActions or ShipActions (without any 'NOACTION')
    """
    def ActionPriority(self,play):
        dic1=self.ActionPriorityList(play)[0]
        dic2=self.ActionPriorityList(play)[1]
        for s in dic1.keys():
            dic1[s]=[a for a in dic1[s] if a!='NOACTION']
        for s in dic2.keys():
            dic2[s]=[a for a in dic2[s] if a!='NOACTION']
        return dic1, dic2

    """
    Return index of non-'NOACTION' actions in ActionPriorityList()
       Parameters:
        play: PlayerID
       Returns:
        Tuple of dictionary with
            Key: ShipId and ShipyardId
            Values: list of int
    """
    def ActionPriorityIndex(self,play):
        dic1=self.ActionPriorityList(play)[0]
        dic2=self.ActionPriorityList(play)[1]
        for s in dic1.keys():
            x=dic1[s]
            dic1[s]=[i for i,d in enumerate(x) if d!='NOACTION']
        for s in dic2.keys():
            y=dic2[s]
            dic2[s]=[i for i,d in enumerate(y) if d!='NOACTION']
        return dic1, dic2

    """
    Return all ships and shipyards with potential problems (shipyard will "collide" if it is spawning)
       Parameters:
        play: PlayerID
       Returns:
        Tuple of list of ShipyardID and ShipId
    """
    def potentialCollisions(self,actionlist):
        shiplist=[]
        for s in actionlist[0].keys():
            if actionlist[0][s][0]!=ShipAction.CONVERT:
                shiplist.append(s)
        shipyardlist=[]
        for s in actionlist[1].keys():
            if actionlist[1][s][0]!=None:
                shipyardlist.append(s)
        return shiplist, shipyardlist

    """    
    Return the cluster around a specified ship, taking into acconut shipyard spawns
       Parameters:
        play: PlayerID
        shiplist: list of ShipId
       Returns:
        Tuple of list of ShipyardID and ShipId
    """

    
    def ShipCluster(self,play, shiplist, shipyardlist, ship,apl): 
#         apl=self.ActionPriority(play)
        clustership=[ship]
        clustershipyard=[]
        sh = [s for s in shiplist if s!=ship]
        for ship1 in sh:
            if apl[0][ship1][0]!=None:
                if apl[0][ship][0]!=None:
                    p1=self.board.ships[ship].position.translate(apl[0][ship][0].to_point(),self.size)
                    p2=self.board.ships[ship1].position.translate(apl[0][ship1][0].to_point(),self.size)
                    if p1==p2:
                        clustership.append(ship1)
                if apl[0][ship][0]==None:
                    if self.board.ships[ship].position==self.board.ships[ship1].position.translate(apl[0][ship1][0].to_point(),self.size):
                        clustership.append(ship1)
            if apl[0][ship1][0]==None:
                if apl[0][ship][0]!=None:
                    if self.board.ships[ship].position.translate(apl[0][ship][0].to_point(),self.size)==self.board.ships[ship1].position:
                        clustership.append(ship1)
        for shipyard1 in shipyardlist:
            if apl[0][ship][0]!=None:
                if self.board.ships[ship].position.translate(apl[0][ship][0].to_point(),self.size)==self.board.shipyards[shipyard1].position:
                    clustershipyard.append(shipyard1)
            if apl[0][ship][0]==None:
                if self.board.ships[ship].position==self.board.shipyards[shipyard1].position:
                    clustershipyard.append(shipyard1)
        return clustership,clustershipyard

    """
    Return the list of clusters (which is a list of lists), taking into account shipyard spawns
       Parameters:
        play: PlayerID
       Returns:
        List of List of ShipyardId and ShipId
    """
    def ShipClusters(self, play,shiplist, shipyardlist,apl):
        shs=shiplist
        shy=shipyardlist
        clusterlist=[]
        while len(shs)>0:
            ship=shs[0]
            clusterlist.append(self.ShipCluster(play,shs, shy,ship,apl))
            shs = [s for s in shs if s not in self.ShipCluster(play,shs, shy,ship,apl)[0]]
            shy = [s for s in shy if s not in self.ShipCluster(play,shs, shy,ship,apl)[1]]
            if len(shs)>0:
                ship=shs[0]
        cc=[cl for cl in clusterlist if sum([len(sublist) for sublist in cl])>1]
        return cc
    
    """
    Return the clusters of ships that will collide with other ships in next board step (using most prioritized in a list of prescribed action)
       Parameters:
        play: PlayerId
        actionlist: list of list of ShipyardActions and ShipyardActions (one list for each element in play.ship_ids+play.shipyard_ids)
       Returns:
        List of List of ShipId and ShipyardId
    """
    def helper1(self,actionlist): #action is tuple of list of actions for shipid,shipyardid
        shiplist=self.potentialCollisions(actionlist)[0]
        shipyardlist=self.potentialCollisions(actionlist)[1]
#         shiplist_cpy=potentialCollisions(play,actionlist)[0]
#         shipyardlist_cpy=potentialCollisions(play,actionlist)[1]
#         board_cpy=board
#         nonupdatedactionlist=[]
#         for ship in shiplist_cpy:
#             board_cpy.ships[ship].next_action=actionlist[0][ship][0]
#             nonupdatedactionlist.append(actionlist[0][ship][0])
#         for shipyard in shipyardlist_cpy:
#             board_cpy.shipyards[shipyard].next_action=actionlist[1][shipyard][0]
#         board_cpy=board_cpy.next() # needed to take into account shipyard spawning ships
#         allpos=[board_cpy.ships[s].position.translate(actionlist[0][s][0],size) for s in shiplist].extend([board_cpy.shipyards[s].position for s in board_cpy.shipyards.keys() if s in shipyardlist]) #positions of shipyard and ships in shiplist
        allpos=[]
        for s in shiplist:
            if actionlist[0][s][0]!=None:
                pos1=self.board.ships[s].position.translate(actionlist[0][s][0].to_point(),self.size)
                allpos.append(pos1)
            if actionlist[0][s][0]==None:
                pos2=self.board.ships[s].position
                allpos.append(pos2)
        for sy in shipyardlist:
            pos3=self.board.shipyards[sy].position
            allpos.append(pos3)
        allposbad=set([x for x in allpos if allpos.count(x)>1])
    #         if board.step<=10:
    #             print('step', board.step,allpos, allposbad)
        return allposbad
    
    def HighPriorityCollisions(self,actionlist): #action is tuple of list of actions for shipid,shipyardid
        shiplist=self.potentialCollisions(actionlist)[0]
        shipyardlist=self.potentialCollisions(actionlist)[1]
#         shiplist_cpy=potentialCollisions(play,actionlist)[0]
#         shipyardlist_cpy=potentialCollisions(play,actionlist)[1]
#         board_cpy=board
#         nonupdatedactionlist=[]
#         for ship in shiplist_cpy:
#             board_cpy.ships[ship].next_action=actionlist[0][ship][0]
#             nonupdatedactionlist.append(actionlist[0][ship][0])
#         for shipyard in shipyardlist_cpy:
#             board_cpy.shipyards[shipyard].next_action=actionlist[1][shipyard][0]
#         board_cpy=board_cpy.next() # needed to take into account shipyard spawning ships
#         allpos=[board_cpy.ships[s].position.translate(actionlist[0][s][0],size) for s in shiplist].extend([board_cpy.shipyards[s].position for s in board_cpy.shipyards.keys() if s in shipyardlist]) #positions of shipyard and ships in shiplist
        posbad=self.helper1(actionlist)
        shipcollide=[]
        shipyardcollide=[]
        for s in shiplist:
            if actionlist[0][s][0]!=None:
                pos1=self.board.ships[s].position.translate(actionlist[0][s][0].to_point(),self.size)
                if pos1 in posbad:
                    shipcollide.append(s)
            if actionlist[0][s][0]==None:
                pos2=self.board.ships[s].position
                if pos2 in posbad:
                    shipcollide.append(s)
        for sy in shipyardlist:
            pos3=self.board.shipyards[sy].position
            if pos3 in posbad:
                shipyardcollide.append(sy)
#         if board.step<=10:
#             print('step', board.step, pos, shipcollide, shipyardcollide)
        return shipcollide, shipyardcollide


    """
    Return ship with lowest priority action in a list of ships
       Parameters:
        shiplist: List of ShipId
        shipactionindex: List of int
       Returns:
        ShipId    #earlyLateGame
    earlyGameTurn = 10
    

    """
    def LowestPriorityShip(self,shiplist, shipactionindex):
        shipss=[s for s in shiplist if len(shipactionindex[s])>0]
        lowestpriorityship=shipss[0]
        for s in shipss:
            if len(shipactionindex[s])>0 and shipactionindex[s][0]>shipactionindex[lowestpriorityship][0]:
                lowestpriorityship=s
        return lowestpriorityship

    
    
    """
    Gives desired next actions for ships (using priority system) after accounting for collision
       Parameters:
        play: PlayerId
       Returns:
        None if shiplist is empty
        Tuple of dictionary with
            Key: Ships and Shipyards
            Values: ShipAction and ShipyardAction (not a list)
    """  
    #inputs list of ships, outputs desired action for ships after accounting for collision
    # Note that `NOACTION` needs to be distinguish from None (perhaps None means no action assigned at that step)
    # For example None should be given in midgame to the EarlyLate slot in action priority
    def SelfCollision(self,play,apl,api):
        if len(play.ship_ids)==0 and len(play.shipyard_ids)==0:
            return None
        checkingrun=sum([len(sublist) for sublist in self.ActionPriorityIndex(play)[0].values()])+sum([len(sublist) for sublist in self.ActionPriorityIndex(play)[1].values()])
#         apl=self.ActionPriority(play)
#         api=self.ActionPriorityIndex(play)
        k=0
        while k<=checkingrun-1: #case where collision exist
            p=self.potentialCollisions(apl)
            pp=self.helper1(apl)
            problems=self.HighPriorityCollisions(apl)
            problemclusters=self.ShipClusters(play,problems[0], problems[1],apl)
            if len(problemclusters)==0:
                break
#             problemclusters=sorted(problemclusters,key=lambda x: len(x[0]+x[1]),reverse=True) #if there is collision, try to fix biggest cluster first
            for l in range(len(problemclusters)):
                pc=problemclusters[l]
                pcactionindexship={s:api[0][s] for s in pc[0]}
                pcactionindexshipy={s:api[1][s] for s in pc[1]}
                if sum([len(sublist) for sublist in pcactionindexship.values()])>0:
                    lps=self.LowestPriorityShip(pc[0],pcactionindexship) #definition of LowestPriorityShip makes sure number of non-'NOACTION' ship actions is >0 in this case
                    if len(api[0][lps])>1:
                        api[0][lps].pop(0) #deletes the most proritized action for lps
                        apl[0][lps].pop(0)
                    if len(api[0][lps])==1: 
                        api[0][lps]=[]
                        if self.board.ships[lps].halite>self.cost:#convert the ship with lowest priority (no nn considered for now)
                            apl[0][lps]=[ShipAction.CONVERT]
                        if self.board.ships[lps].halite<=self.cost:
                            apl[0][lps]=[None]
                if sum([len(sublist) for sublist in pcactionindexship.values()])==0:
                    if sum([len(sublist) for sublist in pcactionindexshipy.values()])>0:
                        lps=self.LowestPriorityShip(pc[1],pcactionindexshipy) #definition of LowestPriorityShip makes sure number of non-'NOACTION' ship actions is >0 in this case
                        if len(api[1][lps])>1:
                            api[1][lps].pop(0) #deletes the most proritized action for lps
                            apl[1][lps].pop(0)
                        if len(api[1][lps])==1: #this should not happen
                            api[1][lps]=[]
                            apl[1][lps]=[None]
                    if sum([len(sublist) for sublist in pcactionindexshipy.values()])==0: #this should never happen
                        break
            k+=1
        designatedactions={s:apl[0][s][0] for s in play.ship_ids}
        designatedactionsy={s:apl[1][s][0] for s in play.shipyard_ids}
        return designatedactions, designatedactionsy
 
    
    # Returns the commands we send to our ships and shipyards
    #         size = config.size
    #         board = Board(obs, config)
    #         me = board.current_player
    #         enemy_ships = [ship for ship in board.ships.values() if ship not in me.ships]
    #         enemy_shipyards = [shipyard for shipyard in board.shipyards.values() if shipyard not in me.shipyards]
    #         cost = 500 #cost of making a ship or shipyard
        
        ################################
        # Imports and helper functions #
        ################################   
        
        #Game variables
        
    #         #retreat
    #         enemyRetreatRadius=2
    #         
    #         #earlyLateGame
    #         earlyGameTurn = 10
    #         
    #         #shipyardDefense
    #         defenderRadius = 4
    #         
    #         #mining
    #         minHaliteToDeposit = 520
    #         collectRadiusToScan = 4
    #         minHaliteToMine = 100
    #         
    #         #spawn
    #         minHaliteToSpawn = 1050
    #         maxShips = 25
    #         maxRoundToSpawn = 270
    #         
    #         #attackShip
    #         enemyCollisionRadius = 2
    #         
    #         #attackShipyard
    #         enemyShipyardCollisionRadius = 4
    #         maxCargoToAllowDestroyingShipyard = 100
        
        #Code
        
    def myAgent(self):
       # if self.board.step<=30:
           # print(self.board.step,self.me.halite)
        nextactions = self.SelfCollision(self.me,self.ActionPriority(self.me),self.ActionPriorityIndex(self.me))
    
        if nextactions!=None:
            for ship in self.me.ships:
                ship.next_action=nextactions[0][ship.id]
            for shipyard in self.me.shipyards:
                shipyard.next_action=nextactions[1][shipyard.id]    
                                           
        return self.me.next_actions

#want to add a layer of true false to call action functions
    
def agent(obs, config):
    A=Agent(obs,config)
    return A.myAgent()

Writing submission.py


In [4]:
from kaggle_environments import make
env = make("halite", debug=True)
env.run(["submission.py", "submission.py", "submission.py", "submission.py"])
env.render(mode="ipython", width=800, height=600)